# Tutorial 08: Creating Custom Environments

This tutorial walks you through the process of creating custom environments in Flow. Custom environments contain specific methods that define the problem space of a task, such as the state and action spaces of the RL agent and the signal (or reward) that the RL algorithm will optimize over. By specifying a few methods within a custom environment, individuals can use Flow to design traffic control tasks of various types, such as optimal traffic light signal timing and flow regulation via mixed autonomy traffic (see the figures below). Finally, these environments are compatible with OpenAI Gym.

The rest of the tutorial is organized as follows: in section 1 walks through the process of creating an environment for mixed autonomy vehicle control where the autonomous vehicles perceive all vehicles in the network, and section two implements the environment in simulation.

<img src="img/sample_envs.png">


## 1. Creating an Environment Class

In this tutorial we will create an environment in which the accelerations of a handful of vehicles in the network are specified by a single centralized agent, with the objective of the agent being to improve the average speed of all vehicle in the network. In order to create this environment, we begin by inheriting the base environment class located in *flow.envs*:

In [1]:
866691# import the base environment class

import os
866691
print(os.environ["SUMO_HOME"])

from flow.envs import Env

# define the environment class, and inherit properties from the base environment class
class myEnv(Env):
    pass

/home/rrishi/sumo_binaries/bin
using fixed init file======================================


`Env` provides the interface for running and modifying a SUMO simulation. Using this class, we are able to start sumo, provide a network to specify a configuration and controllers, perform simulation steps, and reset the simulation to an initial configuration.

By inheriting Flow's base environment, a custom environment for varying control tasks can be created by adding the following functions to the child class: 
* **action_space**
* **observation_space**
* **apply_rl_actions**
* **get_state**
* **compute_reward**

Each of these components are covered in the next few subsections.

### 1.1 ADDITIONAL_ENV_PARAMS

The features used to parametrize components of the state/action space as well as the reward function are specified within the `EnvParams` input, as discussed in tutorial 1. Specifically, for the sake of our environment, the `additional_params` attribute within `EnvParams` will be responsible for storing information on the maximum possible accelerations and decelerations by the autonomous vehicles in the network. Accordingly, for this problem, we define an `ADDITIONAL_ENV_PARAMS` variable of the form:

In [2]:
ADDITIONAL_ENV_PARAMS = {
    "max_accel": 1,
    "max_decel": 1,
}

All environments presented in Flow provide a unique `ADDITIONAL_ENV_PARAMS` component containing the information needed to properly define some environment-specific parameters. We assume that these values are always provided by the user, and accordingly can be called from `env_params`. For example, if we would like to call the "max_accel" parameter, we simply type:

    max_accel = env_params.additional_params["max_accel"]

### 1.2 action_space

The `action_space` method defines the number and bounds of the actions provided by the RL agent. In order to define these bounds with an OpenAI gym setting, we use several objects located within *gym.spaces*. For instance, the `Box` object is used to define a bounded array of values in $\mathbb{R}^n$.

In [3]:
from gym.spaces.box import Box

In addition, `Tuple` objects (not used by this tutorial) allow users to combine multiple `Box` elements together.

In [4]:
from gym.spaces import Tuple

Once we have imported the above objects, we are ready to define the bounds of our action space. Given that our actions consist of a list of n real numbers (where n is the number of autonomous vehicles) bounded from above and below by "max_accel" and "max_decel" respectively (see section 1.1), we can define our action space as follows:

In [5]:
ADDITIONAL_NET_PARAMS = {
    # radius of the circular components
    "radius_ring": 30,
    # number of lanes
    "lanes": 1,
    # speed limit for all edges
    "speed_limit": 80,
    # resolution of the curved portions
    "resolution": 40
}

In [6]:
from flow.networks import Network

class myNetwork(Network):  # update my network class

    def specify_nodes(self, net_params):
        # one of the elements net_params will need is a "radius" value
        r = 200 #net_params.additional_params["radius"]
        y = 20

        # specify the name and position (x,y) of each node
        nodes = [{"id": "center", "x": 0,  "y": 0},
                 {"id": "right", "x": r,  "y": 0},
                 {"id": "bottom", "x": 0,  "y": -r},
                 {"id": "left", "x": -r,  "y": 0},
                 {"id": "top", "x": 0,  "y": r}]
                 
            
            
            
            
            #{"id": "topright", "x": y,  "y": y},
                 #{"id": "bottomright",  "x": y,  "y": -y},
                 #{"id": "topleft",    "x": -y,  "y": y},
                 #{"id": "bottomleft",   "x": -y, "y": -y},
                 #{"id": "toprightright",   "x": r, "y": y},
                 #{"id": "bottomrightright",   "x": r, "y": -y},
                 #{"id": "topleftleft",   "x": -r, "y": y},
                 #{"id": "bottomleftleft",   "x": -r, "y": -y},
                 #{"id": "toptopright",   "x": y, "y": r},
                 #{"id": "toptopleft",   "x": -y, "y": r},
                 #{"id": "bottombottomright",   "x": y, "y": -r},
                 #{"id": "bottombottomleft",   "x": -y, "y": -r},]

        return nodes

In [7]:
# some mathematical operations that may be used
from numpy import pi, sin, cos, linspace

class myNetwork(myNetwork):  # update my network class

    def specify_edges(self, net_params):
        #r = 50 #net_params.additional_params["radius"]
        edgelen = 200#r * pi / 2
        # this will let us control the number of lanes in the network
        lanes = 3 #net_params.additional_params["num_lanes"]
        # speed limit of vehicles in the network
        speed_limit = net_params.additional_params["speed_limit"]

        edges = [
            {#exit
                "id": "exit_edge1", 
                "numLanes": lanes, 
                "speed": speed_limit,
                "from": "center",
                "to": "right", 
                "length": edgelen,
            },
            {
                "id": "enter_edge2", 
                "numLanes": lanes, 
                "speed": speed_limit,
                "from": "left",
                "to": "center",
                "length": edgelen,
            },
            {
                "id": "enter_edge3", 
                "numLanes": lanes, 
                "speed": speed_limit,
                "from": "bottom",
                "to": "center",
                "length": edgelen,
            },
            {#exit
                "id": "exit_edge4",
                "numLanes": lanes,
                "speed": speed_limit,
                "from": "center",
                "to": "top", 
                "length": edgelen,
            },
            {
                "id": "enter_edge1",
                "numLanes": lanes, 
                "speed": speed_limit,
                "from": "right",
                "to": "center",
                "length": edgelen,
            },
            {#exit
                "id": "exit_edge2",
                "numLanes": lanes, 
                "speed": speed_limit,
                "from": "center",
                "to": "left",
                "length": edgelen,
            },
            {#exit
                "id": "exit_edge3", 
                "numLanes": lanes, 
                "speed": speed_limit,
                "from": "center",
                "to": "bottom",
                "length": edgelen,
            },
            {
                "id": "enter_edge4",
                "numLanes": lanes,
                "speed": speed_limit,
                "from": "top",
                "to": "center", 
                "length": edgelen,
            }
        ]

        return edges



### 1.3 observation_space
The observation space of an environment represents the number and types of observations that are provided to the reinforcement learning agent. For this example, we will be observe two values for each vehicle: its position and speed. Accordingly, we need a observation space that is twice the size of the number of vehicles in the network.

### 1.4 apply_rl_actions
The function `apply_rl_actions` is responsible for transforming commands specified by the RL agent into actual actions performed within the simulator. The vehicle kernel within the environment class contains several helper methods that may be of used to facilitate this process. These functions include:
* **apply_acceleration** (list of str, list of float) -> None: converts an action, or a list of actions, into accelerations to the specified vehicles (in simulation)
* **apply_lane_change** (list of str, list of {-1, 0, 1}) -> None: converts an action, or a list of actions, into lane change directions for the specified vehicles (in simulation)
* **choose_route** (list of str, list of list of str) -> None: converts an action, or a list of actions, into rerouting commands for the specified vehicles (in simulation)

For our example we consider a situation where the RL agent can only specify accelerations for the RL vehicles; accordingly, the actuation method for the RL agent is defined as follows:

### 1.5 get_state

The `get_state` method extracts features from within the environments and provides then as inputs to the policy provided by the RL agent. Several helper methods exist within flow to help facilitate this process. Some useful helper method can be accessed from the following objects:
* **self.k.vehicle**: provides current state information for all vehicles within the network
* **self.k.traffic_light**: provides state information on the traffic lights
* **self.k.network**: information on the network, which unlike the vehicles and traffic lights is static
* More accessor objects and methods can be found within the Flow documentation at: http://berkeleyflow.readthedocs.io/en/latest/

In order to model global observability within the network, our state space consists of the speeds and positions of all vehicles (as mentioned in section 1.3). This is implemented as follows:

### 1.6 compute_reward

The `compute_reward` method returns the reward associated with any given state. These value may encompass returns from values within the state space (defined in section 1.5) or may contain information provided by the environment but not immediately available within the state, as is the case in partially observable tasks (or POMDPs).

For this tutorial, we choose the reward function to be the average speed of all vehicles currently in the network. In order to extract this information from the environment, we use the `get_speed` method within the Vehicle kernel class to collect the current speed of all vehicles in the network, and return the average of these speeds as the reward. This is done as follows:

## 2. Testing the New Environment


### 2.1 Testing in Simulation
Now that we have successfully created our new environment, we are ready to test this environment in simulation. We begin by running this environment in a non-RL based simulation. The return provided at the end of the simulation is indicative of the cumulative expected reward when jam-like behavior exists within the netowrk. 

In [8]:
import re
from flow.controllers.routing_controllers import MinicityRouter

from flow.controllers import IDMController, ContinuousRouter, RLController
from flow.core.experiment import Experiment
from flow.core.params import SumoParams, EnvParams, \
    InitialConfig, NetParams
from flow.core.params import VehicleParams
from flow.networks.ring import RingNetwork, ADDITIONAL_NET_PARAMS

from myEnv import myEnv
from flow.envs import AccelEnv

# sim_params = SumoParams(sim_step=0.1, render=False)

# vehicles = VehicleParams()
# vehicles.add(veh_id="rl",
#              acceleration_controller=(RLController, {}),
#              routing_controller=(MinicityRouter, {}),
#              num_vehicles=25)

# env_params = EnvParams(additional_params=ADDITIONAL_ENV_PARAMS)

# additional_net_params = ADDITIONAL_NET_PARAMS.copy()
# net_params = NetParams(additional_params=additional_net_params)

# initial_config = InitialConfig(bunching=20)

# flow_params = dict(
#     exp_tag='ring',
#     env_name=myEnv,  # using my new environment for the simulation
#     network=myNetwork,
#     simulator='traci',
#     sim=sim_params,
#     env=env_params,
#     net=net_params,
#     veh=vehicles,
#     initial=initial_config,
# )

# # number of time steps
# flow_params['env'].horizon = 1500
# exp = Experiment(flow_params)

# # run the sumo simulation
# _ = exp.run(1)

### 2.2 Training the New Environment

Next, we wish to train this environment in the presence of the autonomous vehicle agent to reduce the formation of waves in the network, thereby pushing the performance of vehicles in the network past the above expected return.

The below code block may be used to train the above environment using the Proximal Policy Optimization (PPO) algorithm provided by RLlib. In order to register the environment with OpenAI gym, the environment must first be placed in a separate ".py" file and then imported via the script below. Then, the script immediately below should function regularly.

In [9]:
# :|

**Note**: We do not recommend training this environment to completion within a jupyter notebook setting; however, once training is complete, visualization of the resulting policy should show that the autonomous vehicle learns to dissipate the formation and propagation of waves in the network.

In [ ]:
import json
import ray
from ray.rllib.agents.registry import get_agent_class
from ray.tune import run_experiments
from ray.tune.registry import register_env

from flow.networks.ring import RingNetwork, ADDITIONAL_NET_PARAMS
from flow.utils.registry import make_create_env
from flow.utils.rllib import FlowParamsEncoder
from flow.core.params import SumoParams, EnvParams, InitialConfig, NetParams
from flow.core.params import VehicleParams, SumoCarFollowingParams
from flow.controllers import RLController, IDMController, ContinuousRouter

# time horizon of a single rollout
HORIZON = 1500
# number of rollouts per training iteration
N_ROLLOUTS = 10
# number of parallel workers
N_CPUS = 15


vehicles = VehicleParams()


# We place 25 autonomous vehicles in the network
# vehicles.add(
#     veh_id="rl",
#     acceleration_controller=(RLController, {}),
#     routing_controller=(MinicityRouter, {}),
#     num_vehicles=25)


# Places x number of autonomous vehicles and y number of human-driven vehicles
x = 24
y = 8

if x != 0:
    vehicles.add(
        veh_id="rl",
        acceleration_controller=(RLController, {}),
        routing_controller=(MinicityRouter, {}),
        num_vehicles=x)

if y != 0:
    vehicles.add(
        veh_id="flow",
        acceleration_controller=(IDMController, {}),
        routing_controller=(MinicityRouter, {}),
        num_vehicles=y,
        color="white")

flow_params = dict(
    # name of the experiment
    exp_tag="experiment",

    # name of the flow environment the experiment is running on
    env_name=myEnv,  # <------ here we replace the environment with our new environment

    # name of the network class the experiment is running on
    network=myNetwork,

    # simulator that is used by the experiment
    simulator='traci',

    # sumo-related parameters (see flow.core.params.SumoParams)
    sim=SumoParams(
        sim_step=0.1,
        render=False,
        restart_instance=True,
    ),

    # environment related parameters (see flow.core.params.EnvParams)
    env=EnvParams(
        horizon=HORIZON,
        warmup_steps=0,
        clip_actions=False,
        additional_params={
#             "target_velocity": 50,
            "sort_vehicles": False,
            "max_accel": 1,
            "max_decel": 1,
        },
    ),
                                         
    # network-related parameters (see flow.core.params.NetParams and the
    # network's documentation or ADDITIONAL_NET_PARAMS component)
    net=NetParams(
        additional_params=ADDITIONAL_NET_PARAMS.copy()
    ),

    # vehicles to be placed in the network at the start of a rollout (see
    # flow.core.params.VehicleParams)
    veh=vehicles,

    # parameters specifying the positioning of vehicles upon initialization/
    # reset (see flow.core.params.InitialConfig)
    initial=InitialConfig(
        bunching=20,
    ),
)


def setup_exps():
    """Return the relevant components of an RLlib experiment.

    Returns
    -------
    str
        name of the training algorithm
    str
        name of the gym environment to be trained
    dict
        training configuration parameters
    """
    alg_run = "PPO"

    agent_cls = get_agent_class(alg_run)
    config = agent_cls._default_config.copy()
    config["num_workers"] = N_CPUS
    config["train_batch_size"] = HORIZON * N_ROLLOUTS
    config["gamma"] = 0.999  # discount rate
    config["model"].update({"fcnet_hiddens": [3, 3]})
    config["use_gae"] = True
    config["lambda"] = 0.97
    config["kl_target"] = 0.02
    config["num_sgd_iter"] = 10
    config['clip_actions'] = False  # FIXME(ev) temporary ray bug
    config["horizon"] = HORIZON

    # save the flow params for replay
    flow_json = json.dumps(
        flow_params, cls=FlowParamsEncoder, sort_keys=True, indent=4)
    config['env_config']['flow_params'] = flow_json
    config['env_config']['run'] = alg_run

    create_env, gym_name = make_create_env(params=flow_params, version=0)

    # Register as rllib env
    register_env(gym_name, create_env)
    return alg_run, gym_name, config


alg_run, gym_name, config = setup_exps()
ray.init(num_cpus=N_CPUS + 1)
trials = run_experiments({
    flow_params["exp_tag"]: {
        "run": alg_run,
        "env": gym_name,
        "config": {
            **config
        },
        "checkpoint_freq": 20,
        "checkpoint_at_end": True,
        "max_failures": 999,
        "stop": {
            "training_iteration": 1000,
        },
    }
})


# VISUALIZE ITERATION

# trials = run_experiments({
#     flow_params["exp_tag"]: {
#         "run": alg_run,
#         "env": gym_name,
#         "config": {
#             **config
#         },
#         "restore": "~/ray_results/experiment/248-1000/checkpoint_980/checkpoint-980",
# #         "checkpoint_freq": 20,
#         "checkpoint_at_end": False,
#         "max_failures": 999,
#         "stop": {
#             "training_iteration": 981,
#         },
#     },
# })

2021-03-08 15:14:25,511	WARNING services.py:597 -- setpgrp failed, processes may not be cleaned up properly: [Errno 1] Operation not permitted.
2021-03-08 15:14:25,545	INFO resource_spec.py:216 -- Starting Ray with 14.79 GiB memory available for workers and up to 7.41 GiB for objects. You can adjust these settings with ray.init(memory=<bytes>, object_store_memory=<bytes>).
2021-03-08 15:14:26,252	INFO ray_trial_executor.py:121 -- Trial PPO_myEnv-v0_06b10b5c: Setting up new remote runner.


(pid=14857) using fixed init file======================================
(pid=14857) 2021-03-08 15:14:28,116	INFO trainer.py:371 -- Tip: set 'eager': true or the --eager flag to enable TensorFlow eager execution
(pid=14857) 2021-03-08 15:14:28,453	INFO trainer.py:512 -- Current log_level is WARN. For more information, set 'log_level': 'INFO' / 'DEBUG' or use the -v and -vv flags.
(pid=14857) No routes specified, defaulting to single edge routes.
(pid=14857) Warning: Speed of turning connection 'enter_edge4_0->exit_edge2_0' reduced by 23.49 due to turning radius of 7.70 (length=9.03 angle=90.00)
(pid=14857) Warning: Speed of turning connection 'enter_edge1_0->exit_edge4_0' reduced by 23.49 due to turning radius of 7.70 (length=9.03 angle=90.00)
(pid=14857) Warning: Speed of turning connection 'enter_edge3_0->exit_edge1_0' reduced by 23.49 due to turning radius of 7.70 (length=9.03 angle=90.00)
(pid=14857) Warning: Speed of turning connection 'enter_edge2_0->exit_edge3_0' reduced by 23.49

(pid=14852) Warning: Speed of turning connection 'enter_edge4_0->exit_edge2_0' reduced by 23.49 due to turning radius of 7.70 (length=9.03 angle=90.00)
(pid=14852) Warning: Speed of turning connection 'enter_edge1_0->exit_edge4_0' reduced by 23.49 due to turning radius of 7.70 (length=9.03 angle=90.00)
(pid=14852) Warning: Speed of turning connection 'enter_edge3_0->exit_edge1_0' reduced by 23.49 due to turning radius of 7.70 (length=9.03 angle=90.00)
(pid=14852) Warning: Speed of turning connection 'enter_edge2_0->exit_edge3_0' reduced by 23.49 due to turning radius of 7.70 (length=9.03 angle=90.00)
(pid=14855) Warning: Speed of turning connection 'enter_edge4_0->exit_edge2_0' reduced by 23.49 due to turning radius of 7.70 (length=9.03 angle=90.00)
(pid=14855) Warning: Speed of turning connection 'enter_edge1_0->exit_edge4_0' reduced by 23.49 due to turning radius of 7.70 (length=9.03 angle=90.00)
(pid=14855) Warning: Speed of turning connection 'enter_edge3_0->exit_edge1_0' reduced b

(pid=14852) Warning: Vehicle 'flow_1' performs emergency braking with decel=-14.79 wished=4.50 severity=2.29, time=0.70.
(pid=14852) Warning: Vehicle 'rl_23' performs emergency braking with decel=-15.57 wished=4.50 severity=2.46, time=0.70.
(pid=14855) Warning: Vehicle 'flow_2' performs emergency braking with decel=-15.73 wished=4.50 severity=2.50, time=0.70.
(pid=14850) Warning: Vehicle 'rl_23' performs emergency braking with decel=-14.73 wished=4.50 severity=2.27, time=0.70.
(pid=14852) Warning: Vehicle 'rl_21' performs emergency braking with decel=-16.48 wished=4.50 severity=2.66, time=1.20.
(pid=14861) Warning: Vehicle 'rl_21' performs emergency braking with decel=-15.57 wished=4.50 severity=2.46, time=0.70.
(pid=14854) Warning: Vehicle 'rl_21' performs emergency braking with decel=-15.57 wished=4.50 severity=2.46, time=0.70.
(pid=14854) Warning: Vehicle 'flow_2' performs emergency braking with decel=-14.95 wished=4.50 severity=2.32, time=0.70.
(pid=14864) Warning: Vehicle 'flow_2'

(pid=14850) Warning: Vehicle 'flow_2' performs emergency braking with decel=-15.55 wished=4.50 severity=2.46, time=0.70.
(pid=14859) Warning: Vehicle 'rl_23' performs emergency braking with decel=-14.73 wished=4.50 severity=2.27, time=0.70.
(pid=14859) Warning: Vehicle 'rl_21' performs emergency braking with decel=-15.78 wished=4.50 severity=2.51, time=0.70.
(pid=14851) Warning: Vehicle 'rl_7' performs emergency braking with decel=-13.56 wished=4.50 severity=2.01, time=89.10.
(pid=14853) Warning: Vehicle 'flow_1' performs emergency braking with decel=-19.91 wished=4.50 severity=3.42, time=91.50.
(pid=14853) Warning: Vehicle 'flow_1' performs emergency braking with decel=-34.77 wished=4.50 severity=6.73, time=93.70.
(pid=14852) Warning: Vehicle 'rl_8' performs emergency braking with decel=-14.28 wished=4.50 severity=2.17, time=96.90.
Result for PPO_myEnv-v0_06b10b5c:
  custom_metrics: {}
  date: 2021-03-08_15-14-50
  done: false
  episode_len_mean: 638.6666666666666
  episode_reward_max

...

(pid=14851) Warning: Vehicle 'flow_1' performs emergency braking with decel=-14.82 wished=4.50 severity=2.29, time=0.70.
(pid=14851) Warning: Vehicle 'rl_23' performs emergency braking with decel=-15.59 wished=4.50 severity=2.46, time=0.70.
(pid=14856) Warning: Vehicle 'rl_3' performs emergency braking with decel=-9.76 wished=4.50 severity=1.17, time=19.40.
(pid=14859) Warning: Vehicle 'rl_7' performs emergency braking with decel=-43.16 wished=4.50 severity=8.59, time=31.30.
(pid=14862) Warning: Vehicle 'rl_5' performs emergency braking with decel=-16.51 wished=4.50 severity=2.67, time=25.70.
(pid=14855) Warning: Vehicle 'flow_2' performs emergency braking with decel=-14.72 wished=4.50 severity=2.27, time=0.70.
(pid=14855) Warning: Vehicle 'flow_5' performs emergency braking with decel=-11.79 wished=4.50 severity=1.62, time=0.90.
(pid=14855) Warning: Vehicle 'rl_21' performs emergency braking with decel=-15.64 wished=4.50 severity=2.48, time=1.00.
(pid=14850) Warning: Vehicle 'rl_23' p

(pid=14864) Warning: Teleporting vehicle 'rl_14'; collision with vehicle 'rl_5', lane=':center_14_0', gap=-1.00, time=25.00 stage=move.
(pid=14864) Warning: Vehicle 'rl_14' ends teleporting on edge 'exit_edge2', time 25.00.
(pid=14864) Warning: Speed of turning connection 'enter_edge4_0->exit_edge2_0' reduced by 23.49 due to turning radius of 7.70 (length=9.03 angle=90.00)
(pid=14864) Warning: Speed of turning connection 'enter_edge1_0->exit_edge4_0' reduced by 23.49 due to turning radius of 7.70 (length=9.03 angle=90.00)
(pid=14864) Warning: Speed of turning connection 'enter_edge3_0->exit_edge1_0' reduced by 23.49 due to turning radius of 7.70 (length=9.03 angle=90.00)
(pid=14864) Warning: Speed of turning connection 'enter_edge2_0->exit_edge3_0' reduced by 23.49 due to turning radius of 7.70 (length=9.03 angle=90.00)
(pid=14865) Warning: Teleporting vehicle 'rl_17'; collision with vehicle 'rl_11', lane=':center_4_0', gap=-1.00, time=43.50 stage=move.
(pid=14865) Warning: Vehicle 'rl

(pid=14851) Warning: Teleporting vehicle 'flow_0'; collision with vehicle 'rl_22', lane=':center_1_1', gap=-1.00, time=59.60 stage=move.
(pid=14851) Warning: Vehicle 'flow_0' ends teleporting on edge 'exit_edge3', time 59.60.
(pid=14851) Warning: Speed of turning connection 'enter_edge4_0->exit_edge2_0' reduced by 23.49 due to turning radius of 7.70 (length=9.03 angle=90.00)
(pid=14851) Warning: Speed of turning connection 'enter_edge1_0->exit_edge4_0' reduced by 23.49 due to turning radius of 7.70 (length=9.03 angle=90.00)
(pid=14851) Warning: Speed of turning connection 'enter_edge3_0->exit_edge1_0' reduced by 23.49 due to turning radius of 7.70 (length=9.03 angle=90.00)
(pid=14851) Warning: Speed of turning connection 'enter_edge2_0->exit_edge3_0' reduced by 23.49 due to turning radius of 7.70 (length=9.03 angle=90.00)
(pid=14865) Warning: Vehicle 'rl_8' performs emergency braking with decel=-16.82 wished=4.50 severity=2.74, time=29.10.
(pid=14859) Warning: Vehicle 'flow_1' performs

(pid=14852) Warning: Vehicle 'rl_21' performs emergency braking with decel=-15.58 wished=4.50 severity=2.46, time=0.70.
(pid=14852) Warning: Vehicle 'flow_1' performs emergency braking with decel=-14.85 wished=4.50 severity=2.30, time=0.70.
(pid=14860) Warning: Vehicle 'rl_20' performs emergency braking with decel=-15.37 wished=4.50 severity=2.42, time=97.20.
(pid=14850) Warning: Vehicle 'rl_21' performs emergency braking with decel=-14.80 wished=4.50 severity=2.29, time=0.70.
(pid=14850) Warning: Vehicle 'flow_2' performs emergency braking with decel=-15.56 wished=4.50 severity=2.46, time=0.80.
(pid=14859) Warning: Teleporting vehicle 'rl_11'; collision with vehicle 'rl_17', lane=':center_14_0', gap=-1.00, time=33.10 stage=move.
(pid=14859) Warning: Vehicle 'rl_11' ends teleporting on edge 'exit_edge2', time 33.10.
(pid=14859) Warning: Speed of turning connection 'enter_edge4_0->exit_edge2_0' reduced by 23.49 due to turning radius of 7.70 (length=9.03 angle=90.00)
(pid=14859) Warning:

(pid=14855) Warning: Vehicle 'flow_0' performs emergency braking with decel=-14.95 wished=4.50 severity=2.32, time=0.70.
(pid=14855) Warning: Vehicle 'flow_2' performs emergency braking with decel=-15.09 wished=4.50 severity=2.35, time=0.80.
(pid=14851) Warning: Vehicle 'rl_23' performs emergency braking with decel=-15.17 wished=4.50 severity=2.37, time=0.70.
(pid=14851) Warning: Vehicle 'rl_21' performs emergency braking with decel=-15.78 wished=4.50 severity=2.51, time=0.70.
(pid=14856) Warning: Vehicle 'flow_1' performs emergency braking with decel=-15.56 wished=4.50 severity=2.46, time=0.70.
(pid=14856) Warning: Vehicle 'flow_2' performs emergency braking with decel=-15.00 wished=4.50 severity=2.33, time=0.90.
(pid=14864) Warning: Vehicle 'flow_4' performs emergency braking with decel=-14.23 wished=4.50 severity=2.16, time=48.40.
(pid=14860) Warning: Teleporting vehicle 'rl_10'; collision with vehicle 'rl_12', lane=':center_16_0', gap=-1.00, time=139.10 stage=move.
(pid=14860) Warn

In [ ]:
# trials = run_experiments({
#     flow_params["exp_tag"]: {
#         "run": alg_run,
#         "env": gym_name,
#         "config": {
#             **config
#         },
#         "restore": "/ray_results/stabilizing_the_ring/TestE/checkpoint_500/checkpoint-500"
#         "checkpoint_freq": 1,
#         "checkpoint_at_end": False,
#         "max_failures": 999,
#         "stop": {
#             "training_iteration": 1,
#         },
#     },
# })